<a id="top" style="float:left;" href="http://dynfluid.ensam.eu/"><img style="height:100px;" src="https://hpp.education/Lessons/omnes-docet-ubique.png"/></a>
<a style="float:right;" href="http://www.cnam.fr//"><img style="height:80px;" src="https://upload.wikimedia.org/wikipedia/commons/6/66/Logo_cnam.gif"/></a>
<center></center>

In [ ]:
from IPython.core.display import HTML
style=open('notebooks.css', "r").read()
HTML(style)

<center>
<h3 style="color:#888888;"> <i>--  Mécanique du Vol  --</i> </h3>
<h1> TP n°1 </h1>
<h3> Introduction au calcul de trajectoire </h3>
<h4>  </h4>
<h6><a href="mailto:simon.marie@lecnam.net">simon.marie@lecnam.net</a></h6>
</center>

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import scipy
#Option pour afficher les figures dans le notebook et eviter le plt.show():
%matplotlib inline
fs=24
plt.rc('xtick', labelsize=fs)
plt.rc('ytick', labelsize=fs)

On se propose dans ce TP de se familiariser avec l'environement de Jupyter et de Python en calculant numériquement la trajectoire d'un projectile. Ce TP est une introduction au calcul de trajectoire et servira de base pour l'étude des phases importantes de la mécanique du vol.


# 1 - Position du problème

Considérons un projectile légèrement planant catapulté avec une force $\mathbf{C_0}$ initiale orientée dans la direction $\theta_0$. Le projectile est soumis à son poid $\mathbf{P}=m\mathbf{g}$ et aux forces aérodynamique de trainée et de portance $\mathbf{F_D}$ et $\mathbf{F_L}$ dont on donne les coefficients. On considérera que la force  exercée par la catapulte agit sur le projectile pendant une durée $t_0=1$s.
Le principe fondamentale de la dynamique appliqué à ce projectile donne:

$$
m\dfrac{d\mathbf{U}}{dt}=\mathbf{C_0}+\mathbf{P}+\mathbf{F_D}+\mathbf{F_L}
$$

La position de l'objet est reliée classiquement à la vitesse par:

$$
\dfrac{d\mathbf{X}}{dt}=\mathbf{U}
$$
Avec $\mathbf{U}=\left(\begin{array}{c}  u_x \\ u_y \end{array}\right)$ et $U=\lVert{\mathbf{U}}\lVert$.


On peut donc écrire le problème sous la forme vectorielle suivante:

$$
\dfrac{d\mathbf{W}}{dt}=\mathbf{K}(\mathbf{W},t)
$$

Avec $\mathbf{W}=\left(\begin{array}{c}  w_1 \\ w_2 \\ w_3 \\ w_4 \end{array}\right)=\left(\begin{array}{c}  x \\ y \\ u_x \\ u_y \end{array}\right)$

En projetant cette équation sur les deux axes du repère $(Oxy)$ on obtient:

$$
\mathbf{K}=
\left\{
\begin{array}{rcl}
K_1&=&u_x\\
K_2&=&u_y\\
K_3&=&\dfrac{C_0\cos(\gamma_0)-F_D\cos(\gamma)-F_L\sin(\gamma)}{m} \\
K_4&=&\dfrac{C_0\sin(\gamma_0)-F_D\sin(\gamma)+F_L\cos(\gamma)-mg}{m}
\end{array}
\right.
$$

Avec:
$$F_D=\dfrac{1}{2}\rho U^2 S C_d$$
$$F_L=\dfrac{1}{2}\rho U^2 S C_l$$
$$\gamma=arctan\left(\dfrac{u_y}{u_x}\right)$$

Ainsi, pour connaitre à chaque instant l'Etat $\mathbf{W}$ du projectile, il est nécessaire de connaitre avec précision sa position et sa vitesse. Pour connaitre sa vitesse il est nécessaire de connaitre son accélération, et donc les forces qui s'exercent sur le projectile. Or ces forces dépendent de la vitesse, il est donc impossible de résoudre analytiquement ce problème.

On utilise donc des approximations successives en décomposant le temps en **itérations**. On se propose d'étudier dans ce TP les méthodes pour calculer une trajectoire et mettre à jour $\mathbf{W}$ à chaque instant.

# 2 - Résolution numérique

On défini les paramètres suivants qui serviront de référence pendant le TP:

In [ ]:
m=1.            # Masse de 1kg
D=0.1           # Diametre de la sphere
g=9.81          # Acceleration de la pesanteur
S=np.pi*D**2/4. # Surface de référence
rho=1.22        # Masse volumique standard de l'air
Cd=0.05         # Coeff de trainée
Cl=0.05         # Coeff de portance

# Propulsion:
C0=80           # Force du catapultage
t0=2            # Temps du catapultage
gamma0=np.pi/6  # Angle du catapultage

Le principe de l'intégration temporelle par itération est basé sur la procédure suivante:

1. Je connais l'état $W$ du projectile à l'itération $n$
2. J'en déduis le bilan des forces qui s'exercent sur celui-ci: Calcul de K(W,t) =>  Je connais donc l'accélération.
3. Je calcul donc l'état $W$ à l'itération $n+1$
4. Je recommence à l'étape 1


Pour réaliser l'étape 2. il faut donc créer une fonction qui calcul le bilan des forces et renvoi l'accélération sur les deux axes $x$ et $y$:


**Définir la fonction K(W,t) permettant de calculer les 4 composantes du vecteur:**

In [ ]:
def K(W,t):
    #### W est un vecteur d'entrée: W=[x,y,ux,uy]
    U2=W[2]**2+W[3]**2 # Norme de la vitesse au carré
    Fd=0.5*rho*U2*S*Cd # Trainée
    Fl=0.5*rho*U2*S*Cl # Portance
    ## La force de catapultage n'est présent que pdt le tps t0
    if t<=t0:
        C=C0
    else:
        C=0
    # Calcul de la pente du vecteur vitesse:
    gamma=np.arctan2(W[3],W[2])
    K1=W[2]
    K2=W[3]
    K3=(C*np.cos(gamma0)-Fd*np.cos(gamma)-Fl*np.sin(gamma))/m
    K4=(C*np.sin(gamma0)-Fd*np.sin(gamma)+Fl*np.cos(gamma)-m*g)/m
    return np.array([K1,K2,K3,K4])

<h2>Schéma d'Euler</h2>



Le schéma d'euler explicite s'écrit de la façon suivante (Cf cours):

$$
W^{n+1}=W^{n}+\Delta t K(W^{n},t)
$$


Implémenter le schéma d'euler pour la mise à jour de $\mathbf{W}$. Faites varier le pas de temps $dt$. Que remarquez vous ?

En choisissant les paramètres proposés, votre projectile doit retomber à 1870m de son point de départ.

In [ ]:
# Etat initial:
x0=0.0
y0=1.0
ux0=0.0
uy0=0.0

W=np.array([x0,y0,ux0,uy0])
dt=0.01

In [ ]:
t=0
fig=plt.figure(figsize=(16,4))
while W[1]>0:
    t+=dt
    W=W+dt*K(W,t)
    plt.plot(W[0],W[1],'.r')
plt.title(str(t)+": Xmax="+str(W[0]),fontsize=fs)
plt.grid(True)
plt.axis('equal')
plt.ylabel('Altitude',fontsize=fs)
plt.xlabel('Position',fontsize=fs)

Discussion:

La précision de ce type de méthode est proportionelle à $\Delta t^n$. Pour Améliorer la précision on peut donc soit diminuer le pas de temps $\Delta t$ soit augmenter l'ordre $n$ de la méthode. On se propose dans la section suivante d'augmenter l'ordre.

<h2>Schéma de Runge-Kutta</h2>

### RK2

Le schéma de Runge_Kutta permet d'augmenter l'ordre d'intégration et consiste à calculer des étapes intermédiaires entre 2 itérations. (On parle de sous-iterations). Ainsi on peut écrire l'ordre 2 sous la forme:

$$
k_1=K(W^{n},t)\\
k_2=K(W^{n}+\dfrac{k_1\Delta t}{2},t+\dfrac{\Delta t}{2})\\
W^{n+1}=W^{n}+\Delta t k_2
$$


Implémenter le schéma de Runge-Kutta d'ordre 2 et comparer vos résultats avec les précédents:

In [ ]:
# Etat initial:
x0=0.0
y0=1.0
ux0=0.0
uy0=0.0

W=np.array([x0,y0,ux0,uy0])

In [ ]:
t=0
fig=plt.figure(figsize=(16,4))
while W[1]>=0:
    t+=dt
    k1=K(W,t)
    k2=K(W+k1*dt/2.,t+dt/2)
    W=W+dt*k2
    plt.plot(W[0],W[1],'.r')
plt.title(str(t)+": Xmax="+str(W[0]),fontsize=fs)
plt.grid(True)
plt.axis('equal')
plt.ylabel('Altitude',fontsize=fs)
plt.xlabel('Position',fontsize=fs)

----
**Discussions**:

# 3 - Influence des paramètres

Lorsque vous avez bien compris le fonctionement des éléments précédent:
* Essayez de faire varier les paramètres (Propulsion, portance, trainée) en essayant de prédire le résultat.
* Augmentez la valeur de $C_0$ et observez les écarts entre les deux méthodes.


Dans les TP suivants, l'intégration temporelle sera intégrée dans un "simulateur" qui servira à simuler et à étudier les différentes phase de vol d'un avion.

<a id="top" style="float:left;" href="http://dynfluid.ensam.eu/"><img style="height:100px;" src="https://hpp.education/Lessons/omnes-docet-ubique.png"/></a>
<a style="float:right;" href="http://www.cnam.fr//"><img style="height:80px;" src="https://upload.wikimedia.org/wikipedia/commons/6/66/Logo_cnam.gif"/></a>
<center><a href="#top">Retour en haut de la page</a></center>